In [ ]:
import time
import json
import datetime

import pyomo.environ as pyo
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
# Total duration (minutes).
T = 60 * 24 * 5
# Sampling interval (minutes).
dt = 30
time_steps = T // dt

TIMES = np.arange(0, T, dt)

CAPACITY = 2000
CAPACITY_INITIAL = CAPACITY / 4

DEMAND_MIN = -16
DEMAND_MAX = 7
PERIOD = 1440

DEMAND = DEMAND_MIN + (DEMAND_MAX - DEMAND_MIN) / 2 * (
    1 + np.sin(2 * np.pi * TIMES / PERIOD)
)
DEMAND = np.maximum(DEMAND, 0)

In [ ]:
from amplpy import modules

SOLVER = "ipopt"

# Set MOSEKLM_LICENSE_FILE environment variable to the location of mosek.lic.
# SOLVER = "mosek"

# SOLVER = "bonmin"

# SOLVER = modules.find("cplex")
# SOLVER = modules.find("couenne")

## Model

In [ ]:
model = pyo.ConcreteModel()

In [ ]:
# Sets
model.T = pyo.RangeSet(0, len(TIMES) - 1)

In [ ]:
# Variables
model.iflow = pyo.Var(model.T, within=pyo.NonNegativeReals, bounds=(0, 5))
model.oflow = pyo.Var(model.T, within=pyo.NonNegativeReals, bounds=(0, 50))
model.level = pyo.Var(model.T, within=pyo.NonNegativeReals, bounds=(0, CAPACITY))

## Constraints

In [ ]:
model.constraints = pyo.ConstraintList()

# Initial level constraint.
model.constraints.add(model.level[0] == CAPACITY_INITIAL)

# Tank dynamics.
for t in range(1, len(TIMES)):
    model.constraints.add(
        model.level[t] == model.level[t-1] + (model.iflow[t-1] - model.oflow[t-1]) * dt
    )

# Outflow constrained by level in the last step.
model.constraints.add(model.oflow[len(TIMES)-1] <= model.level[len(TIMES)-1] / dt)

## Objective

In [ ]:
def objective(m):
    demand_diff = sum((m.oflow[t] - DEMAND[t])**2 for t in m.T)
    inflow_smooth = sum((m.iflow[t+1] - m.iflow[t])**2 for t in range(len(TIMES)-1))
    return demand_diff + 0.1 * inflow_smooth

model.objective = pyo.Objective(rule=objective, sense=pyo.minimize)

## Optimise

In [ ]:
solver = pyo.SolverFactory(SOLVER)

start = time.perf_counter()
#
results = solver.solve(model, tee=True)
#
end = time.perf_counter()

In [ ]:
print(f"Time: {end - start:.6f} seconds")

In [ ]:
# Handle AMPL solvers.
#
SOLVER = SOLVER.split("/")[-1]

In [ ]:
with open(f"tank-global-pyomo-solution-{str(SOLVER).lower()}.json", "w") as f:
    json.dump(
        {
            "objective": round(pyo.value(model.objective), 3),
            "time": round(end - start, 3),
            "timestamp": datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
        },
        f, indent=4
    )

In [ ]:
results_df = pd.DataFrame({
    "time": TIMES,
    "demand": DEMAND,
    "inflow": [pyo.value(model.iflow[t]) for t in model.T],
    "outflow": [pyo.value(model.oflow[t]) for t in model.T],
    "level": [pyo.value(model.level[t]) for t in model.T],
})

In [ ]:
fig, axes = plt.subplots(3, 1, figsize=(8, 8))

sns.lineplot(
    data=results_df,
    x="time",
    y="inflow",
    drawstyle="steps-pre",
    color="#27ae60",
    ax=axes[0],
)
axes[0].set_title("Inflow Rate")
axes[0].set(ylabel=None)
axes[0].set_ylim(1.25, 3.5)
axes[0].grid(axis="y", color="lightgrey", linestyle="--", linewidth=0.5)

sns.lineplot(
    data=results_df,
    x="time",
    y="demand",
    color="black",
    ax=axes[1],
)
sns.lineplot(
    data=results_df,
    x="time",
    y="outflow",
    drawstyle="steps-pre",
    color="#3498db",
    ax=axes[1],
)
axes[1].set_title("Outflow Rate")
axes[1].set(ylabel=None)

sns.lineplot(
    data=results_df,
    x="time",
    y="level",
    color="black",
    ax=axes[2],
)
axes[2].set_title("Tank Level")
axes[2].set(ylabel=None)

plt.tight_layout()

plt.savefig(f"tank-global-pyomo-solution-{str(SOLVER).lower()}.png", format="png", dpi=300)

plt.show()